In [45]:
import pandas as pd 
import numpy as np 

from sklearn.model_selection import train_test_split
from sklearn.pipeline import Pipeline
from sklearn.compose import ColumnTransformer

from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.impute import SimpleImputer

from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
#from lightgbm import LGBMClassifier 

import matplotlib.pyplot as plt
import seaborn as sns

from sklearn.model_selection import GridSearchCV  
from ydata_profiling import ProfileReport
%matplotlib inline

In [ ]:
df_contract = pd.read_csv("data/contract.csv")
df_internet = pd.read_csv("data/internet.csv")
df_personal = pd.read_csv("data/personal.csv")
df_phone = pd.read_csv("data/phone.csv")

In [4]:
dfs = [df_contract,df_internet,df_personal,df_phone]

for doc in dfs:
    doc.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7043 entries, 0 to 7042
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   customerID        7043 non-null   object 
 1   BeginDate         7043 non-null   object 
 2   EndDate           7043 non-null   object 
 3   Type              7043 non-null   object 
 4   PaperlessBilling  7043 non-null   object 
 5   PaymentMethod     7043 non-null   object 
 6   MonthlyCharges    7043 non-null   float64
 7   TotalCharges      7043 non-null   object 
dtypes: float64(1), object(7)
memory usage: 440.3+ KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5517 entries, 0 to 5516
Data columns (total 8 columns):
 #   Column            Non-Null Count  Dtype 
---  ------            --------------  ----- 
 0   customerID        5517 non-null   object
 1   InternetService   5517 non-null   object
 2   OnlineSecurity    5517 non-null   object
 3   OnlineBackup      5517 non-nu

A continuacion pasaré a hacer un analisis exploratorio de cada df por medio de pandas profiling

In [5]:
profile_contract = ProfileReport(df_contract, title="Reporte EDA contract", explorative=True)
profile_internet = ProfileReport(df_internet, title="Reporte EDA internet", explorative=True)
profile_personal = ProfileReport(df_personal, title="Reporte EDA personal", explorative=True)
profile_phone = ProfileReport(df_phone, title="Reporte EDA phone", explorative=True)

In [6]:
profile_contract.to_notebook_iframe()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 8/8 [00:00<00:00, 45.57it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Aqui podemos observar como la variable objetivo (EndDate) tiene una correlacion positiva con la variable type que se refiere al tipo de plan que contrató

por lo que podriamos asumir que al ser un contrato mensual es mas probable que haya una fecha de termino, ya que anual es mas compromiso 

In [ ]:
mensual_cancelo = df_contract[(df_contract['Type'] == 'Month-to-month') & (df_contract['EndDate'] != "No")]
anual_cancelo = df_contract[(df_contract['Type'] == 'One year') & (df_contract['EndDate'] != "No")]
dos_años_cancelo = df_contract[(df_contract['Type'] == 'Two year') & (df_contract['EndDate'] != "No")]

total_mensual = df_contract[df_contract['Type'] == 'Month-to-month']
total_anual = df_contract[df_contract['Type'] == 'One year']
total_dos_años = df_contract[df_contract['Type'] == 'Two year']

In [38]:
Numero_de_contratos_cancelados = df_contract[df_contract['EndDate'] != "No"]
print(f"numero de contratos cancelados: {len(Numero_de_contratos_cancelados)}")

numero de contratos cancelados: 1869


In [31]:
print (f"Total de clientes que cancelaron contrato mensual: {len(mensual_cancelo)}")
print (f"Total de clientes que cancelaron contrato anual: {len(anual_cancelo)}")
print (f"Total de clientes que cancelaron contrato de dos años: {len(dos_años_cancelo)}")

Total de clientes que cancelaron contrato mensual: 1655
Total de clientes que cancelaron contrato anual: 166
Total de clientes que cancelaron contrato de dos años: 48


In [37]:
print ("proporcion de clientes que cancelaron contrato mensual: ", round(len(mensual_cancelo) / len(total_mensual)* 100),"%")
print ("proporcion de clientes que cancelaron contrato anual:", round(len(anual_cancelo) / len(total_anual)* 100),"%")
print ("proporcion de clientes que cancelaron contrato de dos años: ", round(len(dos_años_cancelo) / len(total_dos_años) * 100),"%")

proporcion de clientes que cancelaron contrato mensual:  43 %
proporcion de clientes que cancelaron contrato anual: 11 %
proporcion de clientes que cancelaron contrato de dos años:  3 %


Aqui podemos ver efectivamente entre mas largo sea el contrato, menor es la tasa de cancelacion 

**INTERNET**

In [8]:
profile_internet.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 8/8 [00:00<00:00, 35.23it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**PERSONAL**


In [9]:
profile_personal.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 5/5 [00:00<00:00, 106.36it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

**PHONE**

In [10]:
profile_phone.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 2/2 [00:00<00:00, 30.04it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Voy a unir todos los dfs en el custumerID para tener todo en una tabla 

In [11]:
df_merged = df_contract.merge(df_personal, on='customerID', how='left')\
                       .merge(df_phone, on='customerID', how='left')\
                       .merge(df_internet, on='customerID', how='left')

In [12]:
df_merged["TotalCharges"] = pd.to_numeric(df_merged["TotalCharges"], errors="coerce")


In [13]:
profile = ProfileReport(df_merged, title="Reporte EDA", explorative=True)
profile.to_notebook_iframe()


Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

100%|██████████| 20/20 [00:00<00:00, 807.11it/s]


Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

Despues de ver las correlaciones de las variables, puedo concluir que Total_charges tiene mucha coorelacion

 type, StreamingMovies, StreamingTV, TechSupport no tienen tanta pero influyen moderadamente

 Las demas tienen un indice de menos de 0.200 y la que no tiene correlacion es la de genero 

 Podria quitar las variables de genero y paperless billing a mi parecer 

In [49]:
cancelar_y_streaming = df_merged[(df_merged['EndDate'] != "No") &  ((df_merged['StreamingMovies'] == "Yes") | (df_merged['StreamingTV'] == "Yes"))]

cancelar_y_streaming = cancelar_y_streaming.groupby(['StreamingMovies', 'StreamingTV']).size().reset_index(name='Count')

cancelar_y_streaming = cancelar_y_streaming.sort_values(by='Count', ascending=False)



print(cancelar_y_streaming)



  StreamingMovies StreamingTV  Count
2             Yes         Yes    571
1             Yes          No    247
0              No         Yes    243


Aqui se puede ver que cuando el plan tiene streaming movies y streaming tv es mas probable que cancelen

In [74]:
pareja = df_merged[["Partner", "EndDate"]]

pareja["Partner"] = pareja["Partner"].replace({"Yes": 1, "No": 0})

pareja["EndDate"] = np.where(pareja["EndDate"] == "No", 0, 1)

pareja.corr()


C:\Users\Pedro Alvarez\AppData\Local\Temp\ipykernel_7864\3079222968.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pareja["Partner"] = pareja["Partner"].replace({"Yes": 1, "No": 0})
C:\Users\Pedro Alvarez\AppData\Local\Temp\ipykernel_7864\3079222968.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pareja["EndDate"] = np.where(pareja["EndDate"] == "No", 0, 1)


Partner   EndDate
Partner  1.000000 -0.150448
EndDate -0.150448  1.000000

Esto nos enseña que hay una relacion negativa leve entre tener pareja y cancelar el contrato, entonces se podria implementar un plan para parejas o algo por el estilo 

Tambien se podria pensar que entre mas tiempo estan con la compañia, mas es probable que se vayan por lo que podrian meter una promocion para socios que ya llevan mucho tiempo, basandonos en la correlacion de total y enddate

**Plan para realizar la tarea**

Realizaré el análisis exploratorio de datos. En esta parte planeo observar qué tanta correlación hay entre la variable objetivo y las demás variables para identificar cuáles podrían eliminarse y así mejorar el desempeño del modelo. Además, utilizaré herramientas como info() y describe() para obtener una primera visión general, así como pandas_profiling para realizar un análisis más profundo de los datasets individuales. También uniré todos los conjuntos de datos en uno solo usando la columna ID.

Extraeré la variable objetivo binarizando la columna EndDate: donde haya un "No" colocaré un 0, y donde haya cualquier otro valor colocaré un 1. Esto me permitirá evitar complicaciones con fechas y regularizar los datos. Crearé una nueva columna para esta variable y eliminaré la original (EndDate).

Para construir el modelo, primero definiré cuáles columnas son numéricas y cuáles categóricas. Después, usaré un pipeline para imputar y estandarizar los datos. También aplicaré un preprocesador que transforme las variables categóricas y numéricas adecuadamente, una vez preparados los datos, emplearé el algoritmo LightGBMClassifier como modelo de clasificación. Este modelo fue seleccionado por su alta velocidad de entrenamiento y eficiencia de memoria, lo que lo hace ideal para conjuntos de datos grandes.

Antes de entrenar el modelo, analizaré si la variable objetivo está desbalanceada. En caso de detectar un desbalance significativo, consideraré aplicar estrategias como técnicas de remuestreo para asegurar un rendimiento equilibrado en ambas clases.

Una vez construido el modelo, dividiré el conjunto de datos en entrenamiento y prueba. Entrenaré el modelo con los datos de entrenamiento y lo evaluaré con el conjunto de prueba.

Evaluaré el desempeño del modelo utilizando la métrica AUC-ROC y su respectiva gráfica.

Ajustaré los hiperparámetros mediante una búsqueda de GridSearch, probando diferentes valores como el número de hojas y la profundidad máxima del modelo.

Finalmente, volveré a probar el modelo ya ajustado con los hiperparámetros seleccionados, para verificar si la métrica AUC-ROC mejora y cumple con el umbral requerido por el proyecto.

